## Модель процессов работы склада товаров

In [ ]:
# -*- coding: utf-8 -*-
import simpy
import random


Создадим класс с описанием процессов -

    * seller - процесс покупки, списания со склада
    * stocktaker - процесс инвертаризации склада и дозаказа
    * deliverer - процесс пополнения склада

In [ ]:
class InvStore:
   def __init__(self, env, op, oq, lt, init): 
       self.env = env 
       self.op = op  # уровень для дозаказа /ordering point 
       self.oq = oq  # объем дозаказа /order quantity 
       self.lt = lt  # ожидание поставки /replenishment lead time 
       self.at_hand = init  # уровень на складе /how many items you have at hand 
       self.loss = 0  # отказы клиентам /opportunity loss 
       self.orders = []  # список дозаказов /list of back orders 

   @property 
   def total(self): 
       return sum(self.orders) +self.at_hand

   def print_state(self): 
       print(f'[{round(self.env.now)}] на складе: {self.at_hand}, дозаказ: {self.orders}, отказы: {self.loss}')
       self.env.log.registr()

   def seller(self):
       while True:
           yield self.env.timeout(random.expovariate(1))
           if self.at_hand > 0:
               self.at_hand -= 1  # продажа клиенту
               self.env.stocktake.succeed()  # сигнал на запрос клиента 
           else:
               self.loss += 1  # отказ в продаже
           self.print_state()  # регистрация в журнале

   def stocktaker(self):
       self.env.stocktake = self.env.event()  # определение события-покупки
       while True:
           yield self.env.stocktake
           if self.total <= self.op:
               self.orders.append(self.oq)
               self.env.process(self.deliverer())  # активизация доставки
           self.env.stocktake = self.env.event()  # восстановление события-покупки

   def deliverer(self):
       self.print_state()  # состояние склада в момент дозаказа
       yield self.env.timeout(random.expovariate(1/self.lt)) # длительность доставки
       if len(self.orders) > 0:
           self.at_hand += self.orders.pop(0)
       self.print_state()  # состояние склада в момент доставки

Создадим класс журналирования

In [5]:
import matplotlib.pyplot as plt

class Log:
   def __init__(self, env): 
       self.env = env 
       self.time, self.at_hand, self.loss, self.total = [],[],[],[]
       self.registr()

   def registr(self): 
       self.time.append(self.env.now) 
       self.at_hand.append(self.env.model.at_hand) 
       self.loss.append(self.env.model.loss) 
       self.total.append(self.env.model.total) 

   def plot_log(self, info=0):
       # ступенчатый график со ступенькой "после"
       plt.step(self.time, self.at_hand, where="post")
       plt.xlabel("время")
       plt.ylabel("запасы")
       # настройка вида текстовой строки на графике:
       args = {'rotation':50,'color':'C3','bbox': {'color': 'white', 'alpha': .5, 'boxstyle': 'round'}}
       plt.text(1, 1, f'отказов\n{info}', **args)
       plt.show()

Запустим модель

* уровень для дозаказа /ordering point  =10
* объем дозаказа /order quantity  =20
* ожидание поставки /replenishment lead time  =7
* нач.уровень запасов /how many items you have at hand  =20

In [ ]:
# periodic inventory store
env = simpy.Environment()
env.model = InvStore(env, 10, 20, 7, 20)  # op, oq, time, init 
env.log = Log(env)
#
env.process(env.model.seller())
env.process(env.model.stocktaker())
env.run(until=300)
#
env.log.plot_log(env.model.loss)